In [1]:
# # This Python 3 environment comes with many helpful analytics libraries installed
# # It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# # For example, here's several helpful packages to load

# import numpy as np # linear algebra
# import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# # Input data files are available in the read-only "../input/" directory
# # For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

# import os
# for dirname, _, filenames in os.walk('/kaggle/input'):
#     for filename in filenames:
#         print(os.path.join(dirname, filename))

# # You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# # You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [3]:
!pip install pytorch-warmup

In [9]:
import math, torch, torchaudio
import soundfile
import torch.nn as nn
import torch.nn.functional as F
import os, numpy
from sklearn import metrics
from operator import itemgetter
import glob, numpy, os, random, soundfile, torch
from scipy import signal
import time
import tqdm
import pytorch_warmup as warmup
from torch.utils.tensorboard import SummaryWriter

In [76]:
class test_loader(object):
    def __init__(self, train_list, train_path, musan_path, rir_path, num_frames, **kwargs):
        self.train_path = train_path
        self.num_frames = num_frames
        # Load and configure augmentation files
#         self.noisetypes = ['noise','speech','music']
#         self.noisesnr = {'noise':[0,15],'speech':[13,20],'music':[5,15]}
#         self.numnoise = {'noise':[1,1], 'speech':[3,8], 'music':[1,1]}
#         self.noiselist = {}
#         augment_files   = glob.glob(os.path.join(musan_path,'*/*/*/*.wav'))
#         for file in augment_files:
#             if file.split('/')[-4] not in self.noiselist:
#                 self.noiselist[file.split('/')[-4]] = []
#             self.noiselist[file.split('/')[-4]].append(file)
#         self.rir_files  = glob.glob(os.path.join(rir_path,'*/*/*.wav'))
        # Load data & labels
        self.data_list  = []
        self.data_label = []
        lines = open(train_list).read().splitlines()
        dictkeys = list(set([x.split()[0] for x in lines]))
        dictkeys.sort()
        dictkeys = { key : ii for ii, key in enumerate(dictkeys) }
        for index, line in enumerate(lines):
            speaker_label = dictkeys[line.split()[0]]
            file_names = line.split()[1:]  # Get the file names from the line
            file_paths = []
            for file_name in file_names:
                full_file_path = os.path.join(train_path, file_name)
                file_paths.append(full_file_path)
            self.data_label.append(speaker_label)
            self.data_list.append(file_paths)  # Append both file paths

    def __getitem__(self, index):
        try:
            # Read the utterance and randomly select the segment
            audio1, sr1 = soundfile.read(self.data_list[index][0])        
            length = self.num_frames * 160 + 240
            if audio1.shape[0] <= length:
                shortage = length - audio1.shape[0]
                audio1 = numpy.pad(audio1, (0, shortage), 'wrap')
            start_frame = numpy.int64(random.random()*(audio1.shape[0]-length))
            audio1 = audio1[start_frame:start_frame + length]
            #audio1 = numpy.stack([audio1], axis=0).astype(numpy.float32)

            # Read the second utterance and randomly select the segment
            audio2, sr2 = soundfile.read(self.data_list[index][1])        
            if audio2.shape[0] <= length:
                shortage = length - audio2.shape[0]
                audio2 = numpy.pad(audio2, (0, shortage), 'wrap')
            start_frame = numpy.int64(random.random()*(audio2.shape[0]-length))
            audio2 = audio2[start_frame:start_frame + length]
            #audio2 = numpy.stack([audio2], axis=0).astype(numpy.float32)

            # Data Augmentation
    #         augtype = random.randint(0,5)
    #         if augtype == 0:   # Original
    #             audio = audio
    #         elif augtype == 1: # Reverberation
    #             audio = self.add_rev(audio)
    #         elif augtype == 2: # Babble
    #             audio = self.add_noise(audio, 'speech')
    #         elif augtype == 3: # Music
    #             audio = self.add_noise(audio, 'music')
    #         elif augtype == 4: # Noise
    #             audio = self.add_noise(audio, 'noise')
    #         elif augtype == 5: # Television noise
    #             audio = self.add_noise(audio, 'speech')
    #             audio = self.add_noise(audio, 'music')
            # Return the two audio files as tensors along with the label

            # Concatenate the two audio files along a new dimension
            concatenated_audio = numpy.stack([audio1, audio2], axis=0).astype(numpy.float32)
            # Convert concatenated_audio and label to tensors
           
            return torch.tensor(concatenated_audio),(self.data_label[index])
        
        except Exception as e:
#         # If an error occurs (e.g., file not found), print a warning and return None
#         print(f"Error processing file {self.data_list[index]}: {e}")
            length = self.num_frames * 160 + 240
            return torch.zeros((2, length)), self.data_label[index]
        

    def __len__(self):
        return len(self.data_list)

    def add_rev(self, audio):
        rir_file    = random.choice(self.rir_files)
        rir, sr     = soundfile.read(rir_file)
        rir         = numpy.expand_dims(rir.astype(numpy.float32),0)
        rir         = rir / numpy.sqrt(numpy.sum(rir**2))
        return signal.convolve(audio, rir, mode='full')[:,:self.num_frames * 160 + 240]

    def add_noise(self, audio, noisecat):
        clean_db    = 10 * numpy.log10(numpy.mean(audio ** 2)+1e-4) 
        numnoise    = self.numnoise[noisecat]
        noiselist   = random.sample(self.noiselist[noisecat], random.randint(numnoise[0],numnoise[1]))
        noises = []
        for noise in noiselist:
            noiseaudio, sr = soundfile.read(noise)
            length = self.num_frames * 160 + 240
            if noiseaudio.shape[0] <= length:
                shortage = length - noiseaudio.shape[0]
                noiseaudio = numpy.pad(noiseaudio, (0, shortage), 'wrap')
            start_frame = numpy.int64(random.random()*(noiseaudio.shape[0]-length))
            noiseaudio = noiseaudio[start_frame:start_frame + length]
            noiseaudio = numpy.stack([noiseaudio],axis=0)
            noise_db = 10 * numpy.log10(numpy.mean(noiseaudio ** 2)+1e-4) 
            noisesnr   = random.uniform(self.noisesnr[noisecat][0],self.noisesnr[noisecat][1])
            noises.append(numpy.sqrt(10 ** ((clean_db - noise_db - noisesnr) / 10)) * noiseaudio)
        noise = numpy.sum(numpy.concatenate(noises,axis=0),axis=0,keepdims=True)
        return noise + audio
    
#     def my_collate_fn(self, batch):
#         # Filter out None values from the batch
#         batch = [b for b in batch if b is not None]
#         # Convert non-None values to tensors using torch.as_tensor()
#         return [(torch.as_tensor(b[0]), b[1], b[2]) for b in batch]

In [83]:
import torch
from torch.utils.data import DataLoader
from sklearn.metrics import roc_curve

# Check if CUDA is available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)

# Define your collate function
def my_collate_fn(batch):
    # Filter out None values from the batch
    batch = [b for b in batch if b is not None]
    # Convert non-None values to tensors using torch.as_tensor()
    return [torch.as_tensor(data) for data in batch]

# def my_collate_fn(batch):
#         # Filter out None values from the batch
#         batch = [b for b in batch if b is not None]
        
#         # Convert non-None values to tensors using torch.as_tensor()
#         return [torch.as_tensor(b) for b in batch]


testloader = test_loader("/kaggle/input/voxceleb-h/voxceleb_h.txt", "/kaggle/input/voxceleb1train/wav", None, None, 300)
testLoader = DataLoader(testloader, batch_size=128, shuffle=False, num_workers=10) #collate_fn = my_collate_fn,

Using device: cuda


In [84]:
num_files = len(testloader)
print("Number of files in testloader:", num_files)

Number of files in testloader: 552536


In [85]:
#testloader = test_loader("/kaggle/input/voxceleb-h/voxceleb_h.txt", "/kaggle/input/voxceleb1train/wav", None, None, 300)
iteration_count = 0
for batch in testloader:
    inputs = batch[0]  # Assuming inputs are at index 0
    target = batch[1]  # Assuming targets are at index 1
    if inputs is None or target is None:
        continue
    # Your code here

   
    print("Iteration:", iteration_count)
    iteration_count += 1
    # Your remaining code here

    print("inputs:", inputs)
    print("Target:", target)
    
    if iteration_count == 10:
        break
    
# Input: tensor([ 0.0028,  0.0027,  0.0027,  ..., -0.0038, -0.0066, -0.0106])
# Input shape: torch.Size([48240])
# Target: 1

Iteration: 0
inputs: tensor([[-0.0925, -0.0824, -0.0703,  ...,  0.0031, -0.0045, -0.0113],
        [ 0.1183,  0.1589,  0.1053,  ...,  0.0880,  0.0249,  0.0203]])
Target: 1
Iteration: 1
inputs: tensor([[-0.0537, -0.0311,  0.0006,  ..., -0.0071, -0.0078, -0.0072],
        [ 0.0081,  0.0088,  0.0106,  ..., -0.0178,  0.0285, -0.0226]])
Target: 0
Iteration: 2
inputs: tensor([[ 1.3733e-03, -5.7373e-03, -9.8877e-03,  ...,  4.9225e-02,
          3.9490e-02,  3.0273e-02],
        [-4.5776e-04, -9.1553e-05,  1.8311e-04,  ..., -9.9579e-02,
         -7.9620e-02, -3.9551e-02]])
Target: 1
Iteration: 3
inputs: tensor([[-0.1399, -0.0969, -0.0565,  ..., -0.0075, -0.0063, -0.0089],
        [-0.0068,  0.0015,  0.0149,  ..., -0.0015, -0.0038, -0.0056]])
Target: 0
Iteration: 4
inputs: tensor([[ 0.0438,  0.0453,  0.0444,  ..., -0.0068, -0.0072, -0.0062],
        [-0.0046, -0.0043, -0.0010,  ..., -0.0266, -0.0295, -0.0220]])
Target: 1
Iteration: 5
inputs: tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 

In [86]:
## Model finetuned on voxceleb1 dataset

#microsoft/unispeech-sat-base-sv
#microsoft/wavlm-base-sv
#microsoft/wavlm-base-plus-sv

In [87]:
import torch
import numpy as np
from sklearn.metrics import roc_curve

# Load the feature extractor and model
from transformers import Wav2Vec2FeatureExtractor, UniSpeechSatForXVector

feature_extractor = Wav2Vec2FeatureExtractor.from_pretrained('microsoft/unispeech-sat-base-plus-sv')
model = UniSpeechSatForXVector.from_pretrained('microsoft/unispeech-sat-base-plus-sv')


# Move model and feature extractor to CUDA if available
model.to(device)

Some weights of the model checkpoint at microsoft/unispeech-sat-base-plus-sv were not used when initializing UniSpeechSatForXVector: ['unispeech_sat.encoder.pos_conv_embed.conv.weight_g', 'unispeech_sat.encoder.pos_conv_embed.conv.weight_v']
- This IS expected if you are initializing UniSpeechSatForXVector from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing UniSpeechSatForXVector from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of UniSpeechSatForXVector were not initialized from the model checkpoint at microsoft/unispeech-sat-base-plus-sv and are newly initialized: ['unispeech_sat.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'unispeech_sat.encoder.pos_conv_embed.conv.par

UniSpeechSatForXVector(
  (unispeech_sat): UniSpeechSatModel(
    (feature_extractor): UniSpeechSatFeatureEncoder(
      (conv_layers): ModuleList(
        (0): UniSpeechSatGroupNormConvLayer(
          (conv): Conv1d(1, 512, kernel_size=(10,), stride=(5,), bias=False)
          (activation): GELUActivation()
          (layer_norm): GroupNorm(512, 512, eps=1e-05, affine=True)
        )
        (1-4): 4 x UniSpeechSatNoLayerNormConvLayer(
          (conv): Conv1d(512, 512, kernel_size=(3,), stride=(2,), bias=False)
          (activation): GELUActivation()
        )
        (5-6): 2 x UniSpeechSatNoLayerNormConvLayer(
          (conv): Conv1d(512, 512, kernel_size=(2,), stride=(2,), bias=False)
          (activation): GELUActivation()
        )
      )
    )
    (feature_projection): UniSpeechSatFeatureProjection(
      (layer_norm): LayerNorm((512,), eps=1e-05, elementwise_affine=True)
      (projection): Linear(in_features=512, out_features=768, bias=True)
      (dropout): Dropout(p=0.

In [88]:
import torch
import numpy as np
from sklearn.metrics import roc_curve

# Assuming testLoader provides input tensors and targets
# Adjust according to your data loading mechanism
with torch.no_grad():
    similarities = []
    labels = []
    for inputs, target in testLoader:
        #print("Inputs:", inputs)
        #print("Target:", target)
        if inputs is None or target is None:
            continue
            
        # Extract audio1 and audio2 from inputs
        audio1 = inputs[:, 0]  
        audio2 = inputs[:, 1]  
        
        # Pass the input tensors to the model
        audio1 = torch.tensor(audio1)
        audio2 = torch.tensor(audio2)
        #print("audio1 shape", audio1.shape)
        
        # Extract embeddings
        audio1 = feature_extractor(audio1, return_tensors="pt", sampling_rate=16000)
        audio1 = audio1.input_values.squeeze(0) 
       
        audio2 = feature_extractor(audio2, return_tensors="pt", sampling_rate=16000)
        audio2 = audio2.input_values.squeeze(0) 
        
        audio1 = audio1.clone().detach().to(device)
        audio2 = audio2.clone().detach().to(device)
        
        # Get embeddings for audio1
        #print("audio1 shape after embedding extraction", audio1.shape)
        outputs_audio1 = model(input_values=audio1)
        embeddings_audio1 = outputs_audio1.embeddings
        embeddings_audio1 = torch.nn.functional.normalize(embeddings_audio1, dim=-1).cpu()
        
        # Get embeddings for audio2
        outputs_audio2 = model(input_values=audio2)
        embeddings_audio2 = outputs_audio2.embeddings
        embeddings_audio2 = torch.nn.functional.normalize(embeddings_audio2, dim=-1).cpu()
        
        # Calculate cosine similarity between embeddings
        similarity = torch.nn.functional.cosine_similarity(embeddings_audio1, embeddings_audio2, dim=-1)
        
        print("Similarity:", similarity)
        print("Label:", target)
        
        similarities.extend(similarity.tolist())
        labels.extend(target.tolist())  # Append the tensor itself, not its item

# Convert lists to numpy arrays
similarities = np.array(similarities)
labels = np.array(labels)

# Calculate ROC curve
fpr, tpr, thresholds = roc_curve(labels, similarities, pos_label=1)

# Find EER
eer_threshold = thresholds[np.argmin(np.abs(fpr - (1 - tpr)))]
eer = (fpr[np.argmin(np.abs(fpr - (1 - tpr)))] + (1 - tpr)[np.argmin(np.abs(fpr - (1 - tpr)))]) / 2

print("Equal Error Rate (EER): {:.2f}%".format(eer * 100))


/tmp/ipykernel_34/2572936547.py:21: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  audio1 = torch.tensor(audio1)
/tmp/ipykernel_34/2572936547.py:22: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  audio2 = torch.tensor(audio2)


Similarity: tensor([0.9188, 0.6835, 0.9096, 0.7461, 0.9143, 1.0000, 0.9150, 0.6507, 0.9769,
        0.6395, 0.9543, 0.7679, 0.9191, 0.6378, 0.9551, 0.7389, 0.9751, 0.5640,
        0.9332, 0.7797, 0.9055, 0.6771, 0.9730, 0.7292, 0.9204, 0.8182, 0.9650,
        0.7061, 0.9316, 0.5526, 0.9631, 0.6791, 0.9356, 0.5535, 0.9673, 0.4494,
        0.9660, 0.7725, 0.9630, 0.7181, 0.9823, 0.4436, 0.9576, 1.0000, 0.9658,
        1.0000, 0.9686, 0.8004, 0.9452, 0.7620, 0.8965, 0.7636, 0.9429, 0.6801,
        0.9357, 1.0000, 0.9133, 0.8040, 0.9600, 0.7660, 0.9148, 0.5055, 0.8935,
        0.7733, 0.9485, 0.6106, 0.9550, 0.6193, 0.9249, 0.7443, 0.9775, 0.6069,
        0.9661, 1.0000, 0.9097, 0.7192, 0.9341, 1.0000, 0.9592, 0.7530, 0.9595,
        0.7010, 0.9695, 0.7072, 0.9622, 0.6098, 0.9822, 0.6687, 0.9363, 0.7626,
        0.9657, 0.7972, 0.9632, 0.5433, 0.9547, 1.0000, 0.9761, 0.6127, 0.9484,
        0.6125, 0.9747, 0.6678, 0.9645, 0.5450, 0.9271, 0.6196, 0.9376, 0.5939,
        0.9140, 0.6420, 0.94

####